<h1 style="text-align: center;">&nbsp;<img style="font-size: 0.9em;" src="https://www.hospitalitynet.org/picture/153007157/travelers-push-tripadvisor-past-1-billion-reviews-opinions.jpg?t=1587981992" alt="" width="300" height="100" /><span style="font-family: tahoma, arial, helvetica, sans-serif; font-size: large;"><span style="font-size: x-large;">      Webscraping de TripAdvisor</span></span><span style="font-family: tahoma, arial, helvetica, sans-serif; font-size: large;">&nbsp; &nbsp; &nbsp;&nbsp;</span>&nbsp;<img src="https://i0.wp.com/mosefparis1.fr/wp-content/uploads/2022/10/cropped-image-1.png?fit=532%2C540&amp;ssl=1" alt="" width="150" height="150" />&nbsp;</h1>
<p style="text-align: center;">&nbsp; &nbsp; &nbsp; &nbsp; &nbsp;de Lucie Gabagnou et Yanis Rehoune</p>

Dans ce premier notebook, nous effectuons une pipeline ETL (extract transorm and load): 
- Récupération des données en utilisant différentes packages: méthode Selenium + Beautiful Soup vs Scrapy
- Utilisation de Pyspark pour nettoyer les données
- Exportation des données pour EDA et ML

Ce même process a été effectué sur Docker (cf ...)




# Webscraping 

L'approche adoptée pour le webscrapping est la suivante: 
- Trouver les urls des pages (chaque page possédant 30 restaurants)
- Récupérer l'ensemble des urls des restaurants ( en webscrappant les urls de la 1ere étape) 
- Scraper chaque restaurant en utilisant le multiprocessing (pour effectuer la même tache en parallèle) et faire de même pour les pages de commentaires sur tripadvisor. 

Rq: Les fonctions sont présentes dans le script webscrapping.py dans utils.

Certaines cellules prennent plus d'une heure à être éxecutées. Dans ce cas là, nous avons généré des csv et pickle dans le repo data. A la place, nous avons laissé un extrait de quelques observations. 

Dans cette partie, nous présentons un travail préliminaire effectué avec BS4 et Selenium même si finalement, nous avons choisi Scrapy. Pourquoi?

#### Installation de l'environnement

In [1]:
import os
os.getcwd()

'/Users/luciegabagnou/Documents/MOSEF/PYTHON/projet_trip_advisor/sentiment_analysis_tripadvisor/notebooks'

On se positionne à la racine du projet pour mieux accéder aux modules et différents dossiers.

In [2]:
current_path=os.path.dirname(os.getcwd())
os.chdir(current_path)
print(os.getcwd())

/Users/luciegabagnou/Documents/MOSEF/PYTHON/projet_trip_advisor/sentiment_analysis_tripadvisor


In [3]:
!pip install -r requirements.txt

In [4]:
!pip install chromedriver-binary


  Using cached chromedriver-binary-110.0.5481.30.0.tar.gz (5.1 kB)
  Preparing metadata (setup.py) ... done
  Created wheel for chromedriver-binary: filename=chromedriver_binary-110.0.5481.30.0-py3-none-any.whl size=9219460 sha256=8e25c660d77f6b5fdc359bdfb700f7688d9c4de100d3abc8756f8fb10b00d0a7
  Stored in directory: /Users/luciegabagnou/Library/Caches/pip/wheels/bf/53/a6/282cf5384e030f87d0cc8fd38e07ecffabda536351ac6f2f5f
Successfully built chromedriver-binary


### Travaux préliminaires avec Selenium et BS4
On effectue un Webscraping via les packages BS4 et Selenium, qui sont majoritairement utilisés pour cette tâche.

Remarque:
- On utilise le driver du package "undetected driver" qui s'avère plus résilient à tout problème de blocage du site. En effet, webscrapper avec webdriver, avec des options pour le navigateur, nous permet d'avoir moins de problèmes mais n'est tout de même pas satisfaisant. 


##### Page principale




```python

def parse_url(url: str) :
    """
    Opens browser and loads the given url.
    Returns a BeautifulSoup object representing the page's source code.
    """

    driver = uc.Chrome() #Undetected chromedriver (uc)
    driver.get(url)
    time.sleep(random.randint(5,10))
    soup = BeautifulSoup(driver.page_source, 'html.parser')
    return soup



```


In [5]:
import concurrent
import pandas as pd

from scripts.utils import parse_url,flatten
from scripts.scraper.restaurants_scraper import get_max_page_number,get_pages_urls,scrap_caracteristics
from scripts.scraper.reviews_scraper import scrap_comments


Ce code est utilisé dans la majorité des fonctions du notebook. La fonction permet de requêter un url (avec undetected driver) puis de parser l'html. Au final, on obtient un objet de type Soup (BeautifulSoup étant particulièrement facile à utiliser)

In [8]:
""" PAGE PRINCIPALE A WEBSCRAPPER : LES RESTAURANTS PARISIENS / RECUPERATION DE SOUP OBJECT POUR WEBSCRAPPING (BeautifulSoup4) """
tripadvisor_searchlink="https://www.tripadvisor.fr/Restaurants-g187147-Paris_Ile_de_France.html"
soup=parse_url(tripadvisor_searchlink)

##### Récupération des pages (1, 2 ... )

Il n'est pas évident de scrapper de façon dynamique un lien, et tout particulièrement de cliquer sur un bouton. Par conséquent, l'une des techniques pour récupérer les urls des pages a été de modifier le lien principal. En effet, on peut accéder au contenu de la seconde page en mentionnant "oa30": https://www.tripadvisor.fr/Restaurants-g187147-oa30-Paris_Ile_de_France.html. Ainsi, le 30 faisant référence aux 30 élements avant (ceux de la première page), on peut facilement faire varier la requête (oa60 => 3eme page). Au final, on itère avec ```for x in range(60, max_page, 30) ``` (60 étant la valeur initiale, max_page=570 le nombre de page maximal, 30 étant le pas).




In [9]:
"""  RECUPERER£ LES PAGES """ 
max_page=get_max_page_number(soup) #Récupération du maximum de pages pour itérer sur ces pages
url_pages=get_pages_urls(tripadvisor_searchlink,max_page) # Récupération de toutes les pages (des urls)

In [10]:
url_pages

['https://www.tripadvisor.fr/Restaurants-g187147-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa30-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa60-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa90-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa120-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa150-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa180-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa210-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa240-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa270-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa300-Paris_Ile_de_France.html',
 'https://www.tripadvisor.fr/Restaurants-g187147-oa330-Paris_Ile_de_France.html',
 'https://www.tripadvisor

#### Récupération des reviews de tous les restaurants

##### Récupération des urls et principales caractéristiques

On va réaliser la tache scrap_main_elements, qui récupère:
- Le nom du restaurant
- L'url
- Le nombre de commentaires
- Les caractéristiques principales: cuisines et intervalles de prix

Pour gagner en temps, on va effectuer cela via le package concurrent: il s'agit d'un package dédié au multithreading, un système de parallélisation de taches. Dans notre cas, on effectue 10 taches simultanement. Néanmoins, le temps d'execution est relativement long donc on a stocké les informations dans le csv 'scraped_data.csv'


In [11]:
""" with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
    results = list(executor.map(scrap_caracteristics, url_pages))
fetch_data=pd.DataFrame(flatten(results))
fetch_data.to_csv("scraped_data.csv") """

""" EXEMPLE """ 
with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
    fetch_elements= list(executor.map(scrap_caracteristics, url_pages[0:5]))


In [12]:
fetch_data=pd.DataFrame(flatten(fetch_elements))

In [13]:
fetch_data

name  \
0                           Jtépadi   
1                    1. Da Giuseppe   
2                      2. Nell'Arte   
3                         3. Cavale   
4             4. Il Etait Un Square   
..                              ...   
178                   147. Mian Fan   
179                148. L'Empreinte   
180            149. La Bonne Excuse   
181                 150. Le Gabriel   
182  le Beaucour by Tartare Factory   

                                                   url  nb_reviews  \
0    https://www.tripadvisor.fr/Restaurant_Review-g...     53 avis   
1    https://www.tripadvisor.fr/Restaurant_Review-g...    535 avis   
2    https://www.tripadvisor.fr/Restaurant_Review-g...    135 avis   
3    https://www.tripadvisor.fr/Restaurant_Review-g...     90 avis   
4    https://www.tripadvisor.fr/Restaurant_Review-g...  3 960 avis   
..                                                 ...         ...   
178  https://www.tripadvisor.fr/Restaurant_Review-g...    528 avis   
179  https://www.tripadvisor.fr/Restaurant_Review-g...    372 avis   
180  https://www.tripadvisor.fr/Restaurant_Review-g...    770 avis   
181  https://www.tripadvisor.fr/Restaurant_Review-g...    708 avis   
182  https://www.tripadvisor.fr/Restaurant_Review-g...    144 avis   

                                        caracteristics  
0                   53 avis?Fermé aujourd'hui?€€ - €€€  
1        535 avis?Fermé aujourd'hui?Italienne, Pizza?€  
2            135 avis?Ouvert?Italienne, Pizza?€€ - €€€  
3                 90 avis?Ouvert?Française, Européenne  
4    3 960 avis?Fermé aujourd'hui?Française, Steakh...  
..                                                 ...  
178  528 avis?Fermé à l'heure actuelle?Chinoise, As...  
179  372 avis?Fermé à l'heure actuelle?Française, E...  
180  770 avis?Fermé aujourd'hui?Française, Européen...  
181  708 avis?Fermé aujourd'hui?Française, Européen...  
182            144 avis?Ouvert?Française, Bar?€€ - €€€  

[183 rows x 4 columns]

##### Récupération des commentaires
La fonction scrap_comments va nous permettre de récupérer les commentaires d'un nombre de page souhaité maximum (on le fixe à 50 dans notre exemple).

In [14]:
urls_list=fetch_data["url"]

In [15]:
urls_list

0      https://www.tripadvisor.fr/Restaurant_Review-g...
1      https://www.tripadvisor.fr/Restaurant_Review-g...
2      https://www.tripadvisor.fr/Restaurant_Review-g...
3      https://www.tripadvisor.fr/Restaurant_Review-g...
4      https://www.tripadvisor.fr/Restaurant_Review-g...
                             ...                        
178    https://www.tripadvisor.fr/Restaurant_Review-g...
179    https://www.tripadvisor.fr/Restaurant_Review-g...
180    https://www.tripadvisor.fr/Restaurant_Review-g...
181    https://www.tripadvisor.fr/Restaurant_Review-g...
182    https://www.tripadvisor.fr/Restaurant_Review-g...
Name: url, Length: 183, dtype: object

In [16]:

import urllib.request
import requests
import re

def scrap_comments(main_url):
    reviews_customers_pages=[]
    reviews_customers_pages.append(main_url)
    reviews_scraped=[]
    nb_reviews=50
    for x in range(10,nb_reviews, 10):
        url=re.sub(r"Reviews-",f"Reviews-or{x}-",main_url)
        reviews_customers_pages.append(url)
    
    for page in reviews_customers_pages:
        soup=parse_url(page)
        reviews= [title.text+": "+review.text for title,review in zip(soup.find_all("span",class_="noQuotes"),soup.find_all("p","partial_entry"))]
        reviews_scraped.append(reviews)
        print(page)
    return reviews_scraped

In [17]:
urls_list=fetch_data["url"]
"""  
with concurrent.futures.ThreadPoolExecutor(max_workers=4) as executor:
    comments = list(executor.map(scrap_comments, all_restaurants_url))
"""
""" EXEMPLE"""
with concurrent.futures.ThreadPoolExecutor(max_workers=2) as executor:
    comments = list(executor.map(scrap_comments, urls_list.values.tolist()[0:4]))

https://www.tripadvisor.fr/Restaurant_Review-g187147-d20208797-Reviews-Da_Giuseppe-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20096381-Reviews-Jtepadi-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20208797-Reviews-or10-Da_Giuseppe-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20096381-Reviews-or10-Jtepadi-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20208797-Reviews-or20-Da_Giuseppe-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20096381-Reviews-or20-Jtepadi-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20096381-Reviews-or30-Jtepadi-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20208797-Reviews-or30-Da_Giuseppe-Paris_Ile_de_France.html
https://www.tripadvisor.fr/Restaurant_Review-g187147-d20208797-Reviews-or40-Da_Giuseppe-Paris_Ile_de_France.html
https://w

Ensuite, on fait un merge facilement entre le jeu de données précédent et les commentaires. Sachant que l'ordre des urls et le même que celui de la liste finale "comments", on rajoute une colonne "comments" au jeu de données "scraped_data.csv".
Remarque: ce code devient compliqué à gérer: beaucoup d'erreurs interviennent, le driver est long pour le multiprocessing, et tripadvisor parvient à nous bloquer même en utilisant des élements comme un temps de "sleep" aléatoire.


In [18]:
fetch_data["comments"]=pd.Series(flatten(comments))

In [19]:
fetch_data

name  \
0                           Jtépadi   
1                    1. Da Giuseppe   
2                      2. Nell'Arte   
3                         3. Cavale   
4             4. Il Etait Un Square   
..                              ...   
178                   147. Mian Fan   
179                148. L'Empreinte   
180            149. La Bonne Excuse   
181                 150. Le Gabriel   
182  le Beaucour by Tartare Factory   

                                                   url  nb_reviews  \
0    https://www.tripadvisor.fr/Restaurant_Review-g...     53 avis   
1    https://www.tripadvisor.fr/Restaurant_Review-g...    535 avis   
2    https://www.tripadvisor.fr/Restaurant_Review-g...    135 avis   
3    https://www.tripadvisor.fr/Restaurant_Review-g...     90 avis   
4    https://www.tripadvisor.fr/Restaurant_Review-g...  3 960 avis   
..                                                 ...         ...   
178  https://www.tripadvisor.fr/Restaurant_Review-g...    528 avis   
179  https://www.tripadvisor.fr/Restaurant_Review-g...    372 avis   
180  https://www.tripadvisor.fr/Restaurant_Review-g...    770 avis   
181  https://www.tripadvisor.fr/Restaurant_Review-g...    708 avis   
182  https://www.tripadvisor.fr/Restaurant_Review-g...    144 avis   

                                        caracteristics  \
0                   53 avis?Fermé aujourd'hui?€€ - €€€   
1        535 avis?Fermé aujourd'hui?Italienne, Pizza?€   
2            135 avis?Ouvert?Italienne, Pizza?€€ - €€€   
3                 90 avis?Ouvert?Française, Européenne   
4    3 960 avis?Fermé aujourd'hui?Française, Steakh...   
..                                                 ...   
178  528 avis?Fermé à l'heure actuelle?Chinoise, As...   
179  372 avis?Fermé à l'heure actuelle?Française, E...   
180  770 avis?Fermé aujourd'hui?Française, Européen...   
181  708 avis?Fermé aujourd'hui?Française, Européen...   
182            144 avis?Ouvert?Française, Bar?€€ - €€€   

                                              comments  
0    [Soirée amicale: Très bon accueil , cuisine fi...  
1    [Petit dîner: Très bon, patron super sympa! Ra...  
2    [Excellent repas et accueil: Equipe trèqs symp...  
3    [Excellente adresse: Restaurant convivial et a...  
4    [Un excellent moment !: Dîner au Jtepadi suite...  
..                                                 ...  
178                                                NaN  
179                                                NaN  
180                                                NaN  
181                                                NaN  
182                                                NaN  

[183 rows x 5 columns]

### Utilisation de Scrapy
Ce package Python nous a permis de réaliser sans problème notre webscrapping. Cette méthode est largement plus rapide que la première. Pourquoi? 

#### Repo Scrapy
Dans le dossier Scrapy, on trouve différents élements de notre projet de Webscraping dont "spiders". Cela correspond à nos scripts pour parcourir parcourent les pages web et extraire les données. En ligne de commande, on exécute:

``` bash
cd tripadvisor_scraper # The second one in scrapy project
scrapy crawler restaurants_urls_scraper
scrapy crawler reviews_scraper

```
- restaurants_urls_scraper.py (comportant le spider restaurants_urls_scraper) permet de récupérer l'ensemble des urls des restaurants (avec les noms) en scrapant les pages principales des restaurants de Paris. 
Remarque: notre étude s'étend sur les restaurants de Paris dans l'analyse exploratoire. De ce fait, la valeur par défaut de l'argument https://www.tripadvisor.fr/Restaurants-g187147-Paris_Ile_de_France.html.
Toutefois, si on souhaitait faire l'étude des restaurants d'une autre ville, ou bien des activités, il suffit d'effectuer la commande suivante:
```
scrapy crawler restaurants_urls_scraper -a start_url= https://www.tripadvisor.fr/Restaurants-g187147-Paris_Ile_de_France.html
```


- reviews_scraper.py permet de scraper chacun des urls de restaurants comme on a pu le faire précedemment: ```scrapy crawler restaurants_urls_scraper```


Sur le notebook:



In [20]:
os.getcwd()

'/Users/luciegabagnou/Documents/MOSEF/PYTHON/projet_trip_advisor/sentiment_analysis_tripadvisor'

In [21]:
os.chdir(os.getcwd()+"/scripts/scraper/scrapy_tripadvisor_scraper/tripadvisor_scraper")

In [ ]:
! scrapy crawl restaurants_urls_scraper

2023-01-24 22:18:03 [scrapy.utils.log] INFO: Scrapy 2.7.1 started (bot: tripadvisor_scraper)
2023-01-24 22:18:03 [scrapy.utils.log] INFO: Versions: lxml 4.9.2.0, libxml2 2.9.13, cssselect 1.2.0, parsel 1.7.0, w3lib 2.1.1, Twisted 22.10.0, Python 3.11.0 | packaged by conda-forge | (main, Jan 15 2023, 05:44:48) [Clang 14.0.6 ], pyOpenSSL 23.0.0 (OpenSSL 3.0.7 1 Nov 2022), cryptography 39.0.0, Platform macOS-13.0-x86_64-i386-64bit
2023-01-24 22:18:03 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'tripadvisor_scraper',
 'NEWSPIDER_MODULE': 'tripadvisor_scraper.spiders',
 'REQUEST_FINGERPRINTER_IMPLEMENTATION': '2.7',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['tripadvisor_scraper.spiders'],
 'TWISTED_REACTOR': 'twisted.internet.asyncioreactor.AsyncioSelectorReactor'}
2023-01-24 22:18:03 [asyncio] DEBUG: Using selector: KqueueSelector
2023-01-24 22:18:03 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.asyncioreactor.AsyncioSelectorReactor
2023-01-24 22:18:03 [scrapy.u

In [ ]:
! scrapy crawl reviews_scraper